In [1]:
import torch

from torchvision import transforms, utils

import diffusers
from diffusers import AsymmetricAutoencoderKL

from diffusers.utils import load_image

def crop_image_to_nearest_divisible_by_8(img):
    # Check if the image height and width are divisible by 8
    if img.shape[1] % 8 == 0 and img.shape[2] % 8 == 0:
        return img
    else:
        # Calculate the closest lower resolution divisible by 8
        new_height = img.shape[1] - (img.shape[1] % 8)
        new_width = img.shape[2] - (img.shape[2] % 8)
        
        # Use CenterCrop to crop the image
        transform = transforms.CenterCrop((new_height, new_width), interpolation=transforms.InterpolationMode.BILINEAR)
        img = transform(img).to(torch.float32).clamp(-1, 1)
        
        return img
        
to_tensor = transforms.ToTensor()

device = "cuda"
dtype=torch.float16
vae = AsymmetricAutoencoderKL.from_pretrained("vae",torch_dtype=dtype).to(device).eval()

image = load_image("generated.png")

image = crop_image_to_nearest_divisible_by_8(to_tensor(image)).unsqueeze(0).to(device,dtype=dtype)

upscaled_image = vae(image).sample
# Save the reconstructed image
utils.save_image(upscaled_image, "test.png")
print('ok')

The config attributes {'block_out_channels': [128, 256, 512, 768, 768], 'force_upcast': False} were passed to AsymmetricAutoencoderKL, but are not expected and will be ignored. Please verify your config.json configuration file.


ok
